<p style="text-align:center">
    <a href="https://skills.network/?utm_medium=Exinfluencer&utm_source=Exinfluencer&utm_content=000026UJ&utm_term=10006555&utm_id=NA-SkillsNetwork-Channel-SkillsNetworkCoursesIBMDS0321ENSkillsNetwork26802033-2022-01-01" target="_blank">
    <img src="https://cf-courses-data.s3.us.cloud-object-storage.appdomain.cloud/assets/logos/SN_web_lightmode.png" width="200" alt="Skills Network Logo">
    </a>
</p>


# **Hands-on Lab: Interactive Visual Analytics with Folium**


Estimated time needed: **40** minutes


The launch success rate may depend on many factors such as payload mass, orbit type, and so on. It may also depend on the location and proximities of a launch site, i.e., the initial position of rocket trajectories. Finding an optimal location for building a launch site certainly involves many factors and hopefully we could discover some of the factors by analyzing the existing launch site locations.


In the previous exploratory data analysis labs, you have visualized the SpaceX launch dataset using `matplotlib` and `seaborn` and discovered some preliminary correlations between the launch site and success rates. In this lab, you will be performing more interactive visual analytics using `Folium`.


## Objectives


This lab contains the following tasks:

*   **TASK 1:** Mark all launch sites on a map
*   **TASK 2:** Mark the success/failed launches for each site on the map
*   **TASK 3:** Calculate the distances between a launch site to its proximities

After completed the above tasks, you should be able to find some geographical patterns about launch sites.


Let's first import required Python packages for this lab:


In [8]:
import piplite
await piplite.install(['folium'])
await piplite.install(['pandas'])

In [9]:
import folium
import pandas as pd

In [10]:
# Import folium MarkerCluster plugin
from folium.plugins import MarkerCluster
# Import folium MousePosition plugin
from folium.plugins import MousePosition
# Import folium DivIcon plugin
from folium.features import DivIcon

If you need to refresh your memory about folium, you may download and refer to this previous folium lab:


[Generating Maps with Python](https://cf-courses-data.s3.us.cloud-object-storage.appdomain.cloud/IBMDeveloperSkillsNetwork-DV0101EN-SkillsNetwork/labs/v4/DV0101EN-Exercise-Generating-Maps-in-Python.ipynb)


In [12]:
# --- Task 1: Mark all launch sites on a map (no internet required) ---

import pandas as pd
import folium
from folium.plugins import MarkerCluster, MousePosition
from folium.features import DivIcon
from pathlib import Path

# 1) Load data
csv_path = Path("spacex_launch_geo.csv")  # put the file next to the notebook if you have it

if csv_path.exists():
    df_geo = pd.read_csv(csv_path)
    sites = (df_geo[["Launch Site", "Latitude", "Longitude"]]
             .dropna()
             .drop_duplicates("Launch Site")
             .rename(columns={"Launch Site":"site",
                              "Latitude":"lat",
                              "Longitude":"lon"})
             .reset_index(drop=True))
else:
    # Fallback (no download): four main SpaceX launch sites
    sites = pd.DataFrame([
        {"site": "CCAFS SLC 40", "lat": 28.5618571, "lon": -80.5773660},
        {"site": "KSC LC 39A",   "lat": 28.5732550, "lon": -80.6468950},
        {"site": "VAFB SLC 4E",  "lat": 34.6320930, "lon": -120.6108290},
        {"site": "BC LC 1",      "lat": 25.9972640, "lon": -97.1560840},  # Boca Chica (Starbase)
    ])

# 2) Build the map centered on the mean location
center = [sites["lat"].mean(), sites["lon"].mean()]
m = folium.Map(location=center, zoom_start=5, tiles="OpenStreetMap")

# 3) Add nice helpers
MousePosition(position="topright",
              prefix="Lat/Lon",
              separator=" , ",
              num_digits=6).add_to(m)

cluster = MarkerCluster().add_to(m)

# 4) Add a marker (and a small text label) for each site
for _, row in sites.iterrows():
    folium.Marker(
        location=[row.lat, row.lon],
        popup=row.site,
        tooltip=row.site,
        icon=folium.Icon(color="blue", icon="rocket", prefix="fa")
    ).add_to(cluster)

    # Optional: add a small text label next to the marker
    folium.map.Marker(
        [row.lat, row.lon],
        icon=DivIcon(
            icon_size=(150, 36),
            icon_anchor=(0, 0),
            html=f'<div style="font-size: 12px; color: #111;"><b>{row.site}</b></div>',
        )
    ).add_to(m)

m


First, let's try to add each site's location on a map using site's latitude and longitude coordinates


The following dataset with the name `spacex_launch_geo.csv` is an augmented dataset with latitude and longitude added for each site.


In [13]:
# Download and read the `spacex_launch_geo.csv`
from js import fetch
import io

URL = 'https://cf-courses-data.s3.us.cloud-object-storage.appdomain.cloud/IBM-DS0321EN-SkillsNetwork/datasets/spacex_launch_geo.csv'
resp = await fetch(URL)
spacex_csv_file = io.BytesIO((await resp.arrayBuffer()).to_py())
spacex_df=pd.read_csv(spacex_csv_file)

Now, you can take a look at what are the coordinates for each site.


In [14]:
# Select relevant sub-columns: `Launch Site`, `Lat(Latitude)`, `Long(Longitude)`, `class`
spacex_df = spacex_df[['Launch Site', 'Lat', 'Long', 'class']]
launch_sites_df = spacex_df.groupby(['Launch Site'], as_index=False).first()
launch_sites_df = launch_sites_df[['Launch Site', 'Lat', 'Long']]
launch_sites_df

Launch Site        Lat        Long
0   CCAFS LC-40  28.562302  -80.577356
1  CCAFS SLC-40  28.563197  -80.576820
2    KSC LC-39A  28.573255  -80.646895
3   VAFB SLC-4E  34.632834 -120.610745

Above coordinates are just plain numbers that can not give you any intuitive insights about where are those launch sites. If you are very good at geography, you can interpret those numbers directly in your mind. If not, that's fine too. Let's visualize those locations by pinning them on a map.


We first need to create a folium `Map` object, with an initial center location to be NASA Johnson Space Center at Houston, Texas.


In [15]:
# Start location is NASA Johnson Space Center
nasa_coordinate = [29.559684888503615, -95.0830971930759]
site_map = folium.Map(location=nasa_coordinate, zoom_start=10)

We could use `folium.Circle` to add a highlighted circle area with a text label on a specific coordinate. For example,


In [16]:
# Create a blue circle at NASA Johnson Space Center's coordinate with a popup label showing its name
circle = folium.Circle(nasa_coordinate, radius=1000, color='#d35400', fill=True).add_child(folium.Popup('NASA Johnson Space Center'))
# Create a blue circle at NASA Johnson Space Center's coordinate with a icon showing its name
marker = folium.map.Marker(
    nasa_coordinate,
    # Create an icon as a text label
    icon=DivIcon(
        icon_size=(20,20),
        icon_anchor=(0,0),
        html='<div style="font-size: 12; color:#d35400;"><b>%s</b></div>' % 'NASA JSC',
        )
    )
site_map.add_child(circle)
site_map.add_child(marker)

and you should find a small yellow circle near the city of Houston and you can zoom-in to see a larger circle.


Now, let's add a circle for each launch site in data frame `launch_sites`


*TODO:*  Create and add `folium.Circle` and `folium.Marker` for each launch site on the site map


An example of folium.Circle:


`folium.Circle(coordinate, radius=1000, color='#000000', fill=True).add_child(folium.Popup(...))`


An example of folium.Marker:


`folium.map.Marker(coordinate, icon=DivIcon(icon_size=(20,20),icon_anchor=(0,0), html='<div style="font-size: 12; color:#d35400;"><b>%s</b></div>' % 'label', ))`


In [21]:
# Initial the map
site_map = folium.Map(location=nasa_coordinate, zoom_start=5)
# For each launch site, add a Circle object based on its coordinate (Lat, Long) values. In addition, add Launch site name as a popup label

# --- Build launch_sites_df if needed (from spacex_df) ---
try:
    launch_sites_df
except NameError:
    # keep only the columns we need and get one row per site
    launch_sites_df = (
        spacex_df[['Launch Site', 'Lat', 'Long', 'class']]
        .groupby('Launch Site', as_index=False)
        .first()[['Launch Site', 'Lat', 'Long']]
    )

# --- Create the base map centered at NASA JSC (Houston) ---
nasa_coordinate = [29.559684888503615, -95.0830971930759]
site_map = folium.Map(location=nasa_coordinate, zoom_start=5, tiles="OpenStreetMap")

# --- Add a circle + a text label (marker) for each launch site ---
for _, row in launch_sites_df.iterrows():
    coord = [row['Lat'], row['Long']]
    name  = row['Launch Site']

    # circle to highlight the site
    folium.Circle(
        location=coord,
        radius=1000,                 # meters
        color="#d35400",
        weight=2,
        fill=True,
        fill_color="#d35400",
        fill_opacity=0.25,
        popup=folium.Popup(name, max_width=250)
    ).add_to(site_map)

    # text label using DivIcon
    folium.Marker(
        location=coord,
        icon=DivIcon(
            icon_size=(150, 24),
            icon_anchor=(0, 0),
            html=f'<div style="font-size:12px;color:#d35400;"><b>{name}</b></div>'
        )
    ).add_to(site_map)

# Save and display the map even in an untrusted notebook
site_map.save("site_map.html")

#from IPython.display import IFrame, display
#display(IFrame("site_map.html", width="100%", height=600))

# display the map
site_map



The generated map with marked launch sites should look similar to the following:


<center>
    <img src="https://cf-courses-data.s3.us.cloud-object-storage.appdomain.cloud/IBM-DS0321EN-SkillsNetwork/labs/module_3/images/launch_site_markers.png">
</center>


Now, you can explore the map by zoom-in/out the marked areas
, and try to answer the following questions:

*   Are all launch sites in proximity to the Equator line?
*   Are all launch sites in very close proximity to the coast?

Also please try to explain your findings.


In [23]:
# Task 2: Mark the success/failed launches for each site on the map

# --- Task 2: Mark the success/failed launches for each site on the map ---

import folium
from folium.plugins import MarkerCluster

# Re-use the dataframe we already loaded earlier: spacex_df
# Expected columns: ['Launch Site','Lat','Long','class']

# Helper for color by outcome
def outcome_color(c):
    return "green" if int(c) == 1 else "red"

# Start (you can keep the NASA center or re-center by average)
center = [spacex_df['Lat'].mean(), spacex_df['Long'].mean()]
site_map = folium.Map(location=center, zoom_start=5, tiles="OpenStreetMap")

# Cluster to make dense points easier to view
cluster = MarkerCluster().add_to(site_map)

# Add a marker for each launch (success=green, failure=red)
for _, row in spacex_df[['Launch Site', 'Lat', 'Long', 'class']].dropna().iterrows():
    folium.CircleMarker(
        location=[row['Lat'], row['Long']],
        radius=5,
        color=outcome_color(row['class']),
        fill=True,
        fill_color=outcome_color(row['class']),
        fill_opacity=0.8,
        popup=folium.Popup(
            f"<b>{row['Launch Site']}</b><br>"
            f"Outcome: {'Success' if int(row['class'])==1 else 'Failure'}",
            max_width=250
        ),
    ).add_to(cluster)

# Optional: simple legend
legend_html = """
<div style="
 position: fixed; bottom: 30px; left: 30px; width: 160px; 
 z-index: 9999; font-size: 14px; background: white; padding: 8px; 
 border: 1px solid #999; border-radius: 6px;">
<b>Landing outcome</b><br>
<span style="display:inline-block;width:10px;height:10px;background:green;margin-right:6px;"></span>Success<br>
<span style="display:inline-block;width:10px;height:10px;background:red;margin-right:6px;"></span>Failure
</div>
"""
site_map.get_root().html.add_child(folium.Element(legend_html))

# Display (and also save so it shows even if notebook isn't trusted)
site_map.save("task2_launch_outcomes_map.html")
#from IPython.display import IFrame, display
#display(IFrame("task2_launch_outcomes_map.html", width="100%", height=600))
site_map



Next, let's try to enhance the map by adding the launch outcomes for each site, and see which sites have high success rates.
Recall that data frame spacex_df has detailed launch records, and the `class` column indicates if this launch was successful or not


In [24]:
spacex_df.tail(10)

Launch Site        Lat       Long  class
46    KSC LC-39A  28.573255 -80.646895      1
47    KSC LC-39A  28.573255 -80.646895      1
48    KSC LC-39A  28.573255 -80.646895      1
49  CCAFS SLC-40  28.563197 -80.576820      1
50  CCAFS SLC-40  28.563197 -80.576820      1
51  CCAFS SLC-40  28.563197 -80.576820      0
52  CCAFS SLC-40  28.563197 -80.576820      0
53  CCAFS SLC-40  28.563197 -80.576820      0
54  CCAFS SLC-40  28.563197 -80.576820      1
55  CCAFS SLC-40  28.563197 -80.576820      0

Next, let's create markers for all launch records.
If a launch was successful `(class=1)`, then we use a green marker and if a launch was failed, we use a red marker `(class=0)`


Note that a launch only happens in one of the four launch sites, which means many launch records will have the exact same coordinate. Marker clusters can be a good way to simplify a map containing many markers having the same coordinate.


Let's first create a `MarkerCluster` object


In [25]:
marker_cluster = MarkerCluster()


*TODO:* Create a new column in `spacex_df` dataframe called `marker_color` to store the marker colors based on the `class` value


In [26]:

# Apply a function to check the value of `class` column
# If class=1, marker_color value will be green
# If class=0, marker_color value will be red

# --- Task 2: Mark the success/failed launches for each site on the map ---

# 1) Color by class (1 = success -> green, 0 = failure -> red)
spacex_df['marker_color'] = spacex_df['class'].map({1: 'green', 0: 'red'})

# 2) Create/attach a MarkerCluster to the existing map
marker_cluster = MarkerCluster().add_to(site_map)

# 3) Add one marker per launch record
for _, row in spacex_df.iterrows():
    outcome = 'Success' if row['class'] == 1 else 'Failure'
    popup_text = (f"<b>Launch Site:</b> {row['Launch Site']}<br>"
                  f"<b>Outcome:</b> {outcome}")

    # Use small circle markers so overlapping points cluster nicely
    folium.CircleMarker(
        location=[row['Lat'], row['Long']],
        radius=5,
        color=row['marker_color'],
        fill=True,
        fill_color=row['marker_color'],
        fill_opacity=0.8,
        popup=folium.Popup(popup_text, max_width=250),
    ).add_to(marker_cluster)

# Display map (if your environment doesn't render automatically)
site_map


*TODO:* For each launch result in `spacex_df` data frame, add a `folium.Marker` to `marker_cluster`


In [32]:
# Add marker_cluster to current site_map
site_map.add_child(marker_cluster)

# for each row in spacex_df data frame
for _, record in spacex_df.iterrows():
    # create a Marker object with its coordinate
    marker = folium.Marker(
        location=[record['Lat'], record['Long']],
        # customize the marker color by outcome (expects 'marker_color' in the df)
        icon=folium.Icon(color=record['marker_color'], icon='info-sign')
    )
    # add the Marker to the cluster on the site map
    marker_cluster.add_child(marker)

site_map


Your updated map may look like the following screenshots:


<center>
    <img src="https://cf-courses-data.s3.us.cloud-object-storage.appdomain.cloud/IBM-DS0321EN-SkillsNetwork/labs/module_3/images/launch_site_marker_cluster.png">
</center>


<center>
    <img src="https://cf-courses-data.s3.us.cloud-object-storage.appdomain.cloud/IBM-DS0321EN-SkillsNetwork/labs/module_3/images/launch_site_marker_cluster_zoomed.png">
</center>


From the color-labeled markers in marker clusters, you should be able to easily identify which launch sites have relatively high success rates.


In [34]:
# === Robust TASK 3 cell: computes distances and always renders/saves the map ===
import math
import folium
import pandas as pd
from IPython.display import display, HTML

# ---- 0) Make sure we have launch_sites_df and a base map ----
if 'launch_sites_df' not in globals():
    # Rebuild from spacex_df if needed (expects spacex_df with Launch Site, Lat, Long, class)
    if 'spacex_df' not in globals():
        raise RuntimeError("Neither launch_sites_df nor spacex_df is defined. Run earlier cells first.")
    _tmp = spacex_df[['Launch Site', 'Lat', 'Long', 'class']].copy()
    launch_sites_df = (
        _tmp.groupby('Launch Site', as_index=False)
            .first()[['Launch Site', 'Lat', 'Long']]
            .astype({'Lat':'float64','Long':'float64'})
    )

# Pick one site to work with
site_name = 'CCAFS LC-40'  # change to any value in launch_sites_df['Launch Site']

row = launch_sites_df.loc[launch_sites_df['Launch Site'] == site_name]
if row.empty:
    raise ValueError(f"Launch site '{site_name}' not found in launch_sites_df['Launch Site'].")

site_lat = float(row.iloc[0]['Lat'])
site_lon = float(row.iloc[0]['Long'])

# If site_map doesn't exist, create a fresh one centered on the chosen site
if 'site_map' not in globals() or not isinstance(site_map, folium.Map):
    site_map = folium.Map(location=[site_lat, site_lon], zoom_start=10, tiles="OpenStreetMap")

# ---- 1) Example proximities (replace with your own MousePosition reads if required) ----
proximities = {
    'Coastline': (28.5637, -80.5716),
    'Railroad':  (28.5729, -80.5850),
    'City (Cocoa Beach)': (28.3200, -80.6080),
}

# ---- 2) Haversine distance in km ----
def haversine_km(lat1, lon1, lat2, lon2):
    R = 6371.0088
    φ1, φ2 = math.radians(lat1), math.radians(lat2)
    dφ = math.radians(lat2 - lat1)
    dλ = math.radians(lon2 - lon1)
    a = math.sin(dφ/2)**2 + math.cos(φ1)*math.cos(φ2)*math.sin(dλ/2)**2
    return 2 * R * math.asin(math.sqrt(a))

# ---- 3) Draw site, lines, and proximity markers ----
folium.Circle(
    location=[site_lat, site_lon],
    radius=800, color='#d35400', fill=True, fill_opacity=0.15
).add_child(folium.Popup(site_name)).add_to(site_map)

for label, (lat, lon) in proximities.items():
    dist_km = haversine_km(site_lat, site_lon, lat, lon)
    txt = f"{label}<br>{dist_km:.2f} km"

    folium.Marker(
        location=[lat, lon],
        icon=folium.Icon(color='blue', icon='flag'),
        popup=folium.Popup(txt, max_width=250)
    ).add_to(site_map)

    folium.PolyLine(
        locations=[[site_lat, site_lon], [lat, lon]],
        color='blue', weight=3, tooltip=f"{label}: {dist_km:.2f} km"
    ).add_to(site_map)

# ---- 4) Force-render and also save to HTML as a fallback ----
# Inline render (works even if implicit display is suppressed in your env)
display(HTML(site_map._repr_html_()))

# Save to HTML so you can open it if inline display is blocked
outfile = "task3_site_distances.html"
site_map.save(outfile)
print(f"Saved map to {outfile}. If the inline map is still blank, open this file.")


Saved map to task3_site_distances.html. If the inline map is still blank, open this file.


Next, we need to explore and analyze the proximities of launch sites.


Let's first add a `MousePosition` on the map to get coordinate for a mouse over a point on the map. As such, while you are exploring the map, you can easily find the coordinates of any points of interests (such as railway)


In [37]:
from folium.plugins import MousePosition

# Show coordinates (Lat, Long) under the cursor in the map's top-right corner
formatter = "function(num) {return L.Util.formatNum(num, 5);};"

mouse_position = MousePosition(
    position='topright',
    separator='  Long: ',
    empty_string='NaN',
    lng_first=False,
    num_digits=20,
    prefix='Lat:',
    lat_formatter=formatter,
    lng_formatter=formatter,
)

site_map.add_child(mouse_position)

from IPython.display import IFrame

site_map.save('site_map.html')
IFrame('site_map.html', width='100%', height=600)


# render (helps in some environments)
site_map


Now zoom in to a launch site and explore its proximity to see if you can easily find any railway, highway, coastline, etc. Move your mouse to these points and mark down their coordinates (shown on the top-left) in order to the distance to the launch site.


Now zoom in to a launch site and explore its proximity to see if you can easily find any railway, highway, coastline, etc. Move your mouse to these points and mark down their coordinates (shown on the top-left) in order to the distance to the launch site.


In [40]:
from math import sin, cos, sqrt, atan2, radians

def calculate_distance(lat1, lon1, lat2, lon2):
    # approximate radius of earth in km
    R = 6373.0

    lat1 = radians(lat1)
    lon1 = radians(lon1)
    lat2 = radians(lat2)
    lon2 = radians(lon2)

    dlon = lon2 - lon1
    dlat = lat2 - lat1

    a = sin(dlat / 2)**2 + cos(lat1) * cos(lat2) * sin(dlon / 2)**2
    c = 2 * atan2(sqrt(a), sqrt(1 - a))

    distance = R * c
    return distance

*TODO:* Mark down a point on the closest coastline using MousePosition and calculate the distance between the coastline point and the launch site.


In [ ]:
# find coordinate of the closet coastline
# e.g.,: Lat: 28.56367  Lon: -80.57163
# distance_coastline = calculate_distance(launch_site_lat, launch_site_lon, coastline_lat, coastline_lon)

In [41]:
# Create and add a folium.Marker on your selected closest coastline point on the map
# Display the distance between coastline point and launch site using the icon property 
# for example
# distance_marker = folium.Marker(
#    coordinate,
#    icon=DivIcon(
#        icon_size=(20,20),
#        icon_anchor=(0,0),
#        html='<div style="font-size: 12; color:#d35400;"><b>%s</b></div>' % "{:10.2f} KM".format(distance),
#        )
#    )

# --- Pick the launch site to analyze (here: CCAFS SLC-40) ---
site_row = launch_sites_df[launch_sites_df['Launch Site'] == 'CCAFS SLC-40'].iloc[0]
launch_site_lat = float(site_row['Lat'])
launch_site_lon = float(site_row['Long'])

# --- Use the MousePosition readout to set your closest coastline point ---
# Replace these with what you read from the map if you choose another point/site
coastline_lat, coastline_lon = 28.56367, -80.57163   # example near CCAFS SLC-40

# --- Compute distance (in KM) ---
distance_coastline = calculate_distance(
    launch_site_lat, launch_site_lon,
    coastline_lat,   coastline_lon
)

# --- Add a text marker at the coastline point showing the distance ---
distance_marker = folium.Marker(
    [coastline_lat, coastline_lon],
    icon=DivIcon(
        icon_size=(20, 20),
        icon_anchor=(0, 0),
        html=f'<div style="font-size: 12px; color:#d35400;"><b>{distance_coastline:0.2f} KM</b></div>'
    )
)
site_map.add_child(distance_marker)

# --- (Optional) draw a line from launch site to coastline point ---
folium.PolyLine(
    locations=[[launch_site_lat, launch_site_lon], [coastline_lat, coastline_lon]],
    color='blue', weight=2, opacity=0.6
).add_to(site_map)

# Show the map
site_map


*TODO:* Draw a `PolyLine` between a launch site to the selected coastline point


In [42]:
# Coordinates for the line: [launch site] -> [selected coastline point]
coordinates = [
    [launch_site_lat, launch_site_lon],
    [coastline_lat,   coastline_lon]
]

# Create and add the PolyLine
lines = folium.PolyLine(locations=coordinates, weight=2, color='blue', opacity=0.7)
site_map.add_child(lines)

# Display the updated map
site_map


Your updated map with distance line should look like the following screenshot:


<center>
    <img src="https://cf-courses-data.s3.us.cloud-object-storage.appdomain.cloud/IBM-DS0321EN-SkillsNetwork/labs/module_3/images/launch_site_marker_distance.png">
</center>


*TODO:* Similarly, you can draw a line betwee a launch site to its closest city, railway, highway, etc. You need to use `MousePosition` to find the their coordinates on the map first


A railway map symbol may look like this:


<center>
    <img src="https://cf-courses-data.s3.us.cloud-object-storage.appdomain.cloud/IBM-DS0321EN-SkillsNetwork/labs/module_3/images/railway.png">
</center>


A highway map symbol may look like this:


<center>
    <img src="https://cf-courses-data.s3.us.cloud-object-storage.appdomain.cloud/IBM-DS0321EN-SkillsNetwork/labs/module_3/images/highway.png">
</center>


A city map symbol may look like this:


<center>
    <img src="https://cf-courses-data.s3.us.cloud-object-storage.appdomain.cloud/IBM-DS0321EN-SkillsNetwork/labs/module_3/images/city.png">
</center>


In [ ]:
# Create a marker with distance to a closest city, railway, highway, etc.
# Draw a line between the marker to the launch site


In [43]:
# --- pick the launch site we want to work with -------------------------------
selected_site = "CCAFS SLC-40"   # <- change if you want another site

site_row = launch_sites_df[launch_sites_df['Launch Site'] == selected_site].iloc[0]
site_lat, site_lon = float(site_row["Lat"]), float(site_row["Long"])

# --- helper that adds a labeled distance marker + line for any POI -----------
def add_distance_poi(poi_lat, poi_lon, label, color="#d35400"):
    """
    Add a labeled marker at (poi_lat, poi_lon) showing the distance from the
    launch site, and draw a polyline connecting them.
    """
    # compute great-circle distance (km)
    dist_km = calculate_distance(site_lat, site_lon, poi_lat, poi_lon)

    # pretty text we’ll show on the map
    html = f'<div style="font-size: 12px; color:{color};"><b>{label}: {dist_km:0.2f} km</b></div>'

    # marker at the POI
    m = folium.Marker(
        location=(poi_lat, poi_lon),
        icon=DivIcon(icon_size=(250, 24), icon_anchor=(0, 0), html=html)
    )
    site_map.add_child(m)

    # line between launch site and POI
    folium.PolyLine(
        locations=[(site_lat, site_lon), (poi_lat, poi_lon)],
        weight=2, color=color, opacity=0.8
    ).add_to(site_map)

    return dist_km

# --- EXAMPLES ----------------------------------------------------------------
# Use MousePosition (added earlier) to read the lat/long you see on the map,
# then paste them below. I’ve included reasonable defaults you can keep or update.

# 1) Closest coastline to CCAFS SLC-40 (example coords from course prompt)
coast_lat, coast_lon = 28.56367, -80.57163
add_distance_poi(coast_lat, coast_lon, "Coastline")

# 2) NASA Railroad (railway) near the pad (example – adjust if you want)
rail_lat, rail_lon = 28.56330, -80.57480
add_distance_poi(rail_lat, rail_lon, "Railway", color="#2e86c1")

# 3) Samuel C Phillips Pkwy (highway) near the pad (example – adjust if you want)
hwy_lat, hwy_lon = 28.56680, -80.57160
add_distance_poi(hwy_lat, hwy_lon, "Highway", color="#16a085")

# 4) Nearest city (example: Cape Canaveral). You can also pick Melbourne, etc.
city_lat, city_lon = 28.3922, -80.6077  # Cape Canaveral
add_distance_poi(city_lat, city_lon, "Nearest city (Cape Canaveral)", color="#8e44ad")

# Finally, show the map in the output
site_map


After you plot distance lines to the proximities, you can answer the following questions easily:

*   Are launch sites in close proximity to railways?
*   Are launch sites in close proximity to highways?
*   Are launch sites in close proximity to coastline?
*   Do launch sites keep certain distance away from cities?

Also please try to explain your findings.


# Next Steps:

Now you have discovered many interesting insights related to the launch sites' location using folium, in a very interactive way. Next, you will need to build a dashboard using Ploty Dash on detailed launch records.


## Authors


[Pratiksha Verma](https://www.linkedin.com/in/pratiksha-verma-6487561b1/)


<!--## Change Log--!>


<!--| Date (YYYY-MM-DD) | Version | Changed By      | Change Description      |
| ----------------- | ------- | -------------   | ----------------------- |
| 2022-11-09        | 1.0     | Pratiksha Verma | Converted initial version to Jupyterlite|--!>


### <h3 align="center"> IBM Corporation 2022. All rights reserved. <h3/>
